In [1]:
import numpy as np
par = np.load('C:/Users/DELL/Downloads/scenario.npy')  # The file scenario contains the 50 disturbance scenarios generated by Latin sampling
par[0,:] = [60,100,120,220,30,50,50,80]

In [2]:
!pip install casadi
from casadi import *
from random import random, randint, seed
from statistics import mean
from copy import deepcopy
import numpy as np


POP_SIZE        = 360  # population size
MIN_DEPTH       = 2    # minimal initial random tree depth
MAX_DEPTH       = 5    # maximal initial random tree depth
MAX_NODE        = 31   # maximum number of tree components
GENERATIONS     = 300  # maximal number of generations to run evolution
TOURNAMENT_SIZE = 5    # size of tournament for tournament selection
XO_RATE         = 0.8  # crossover rate 
PROB_MUTATION   = 0.2  # per-node mutation probability 

# plant model
Tc_out = MX.sym('Tc_out',2) 
T = MX.sym('T')
Th_out = MX.sym('Th_out',2)
ulast = MX.sym('ulast')

u = MX.sym('u',1)

Tc_in = MX.sym('Tc_in')
wc = MX.sym('wc')
Th_in = MX.sym('Th_in',2)
wh = MX.sym('wh',2)
UA = MX.sym('UA',2)

DT2 = Th_in - Tc_out
DT1 = Th_out - Tc_in
DT_lm = (DT1*DT2*(DT1+DT2)*0.5)**(1/3)

#m = MX.sym('m',4)
#oct = MX.sym('oct',4)
#benz = MX.sym('benz',4)

#f1 = 1 - cumsum(m)
#f2 = 98*cumsum(m) - m*oct
#f3 = m[3]

f1 = -1*Tc_out + Tc_in + UA*DT_lm/(vertcat(u,ulast)*wc*4.2)
f2 = -1*T + mtimes(transpose(vertcat(u,ulast)),Tc_out)
f3 = -1*Th_out + Th_in - vertcat(u,ulast)*(Tc_out - Tc_in)*wc/wh
f4 = -1*ulast + 1 - cumsum(u)
f5 = (Tc_out[0] - Tc_in)**2/(Th_in[0] - Tc_in) - (Tc_out[1] - Tc_in)**2/(Th_in[1] - Tc_in)

# optimization
opts = {}
opts["ipopt.max_iter"] = 200
opts["ipopt.print_level"] = 0
opts["show_eval_warnings"] = 0
opts["print_time"] = 0
#par1 = vertcat(60,100,120,220,30,50,50,80)

T_opt = 0
T_J = 0
for i in range(0, par.shape[0]):
    lim0 = par[i,0]
    lim1 = par[i,1]
    lim2 = par[i,2]
    lim3 = par[i,3]
    lim4 = par[i,4]
    lim5 = par[i,5]
    lim6 = par[i,6]
    lim7 = par[i,7]
    limtemp = max(lim2,lim3)
    
    prob = vertcat(f1,f2,f3,f4)
    prob = substitute(prob,vertcat(Tc_in,wc,Th_in,wh,UA),vertcat(lim0,lim1,lim2,lim3,lim4,lim5,lim6,lim7))
    opt = casadi.nlpsol('solver','ipopt',dict(x = vertcat(Tc_out,T,Th_out,u,ulast), f = -1*T, g = prob),opts)
    sol = opt(x0 = [110,200,100,100,124,0.8,0.2], lbx = [lim0,lim0,lim0,lim0,lim0,0,0], ubx = [lim2,lim3,limtemp,lim2,lim3,1,1], lbg = 0, ubg = 0)
    T_opt += float(sol['x'][2])
    if i == 0:
        x_nom = vertcat(lim2,lim3,float(sol['x'][0]),float(sol['x'][1]),lim0)
    
    probJ = vertcat(f1,f2,f3,f4,f5)
    probJ = substitute(probJ,vertcat(Tc_in,wc,Th_in,wh,UA),vertcat(lim0,lim1,lim2,lim3,lim4,lim5,lim6,lim7))
    optJ = casadi.nlpsol('solver','ipopt',dict(x = vertcat(Tc_out,T,Th_out,u,ulast), f = 1, g = probJ),opts)
    solJ = optJ(x0 = [110,200,100,100,124,0.8,0.2], lbx = [lim0,lim0,lim0,lim0,lim0,0,0], ubx = [lim2,lim3,limtemp,lim2,lim3,1,1], lbg = 0, ubg = 0)
    T_J += float(solJ['x'][2])

print(T_opt)
print(T_J)

# genetic programming
def add(x, y): return x + y
def sub(x, y): return x - y
def mul(x, y): return x * y
def div(x, y): return x / y
FUNCTIONS = [add, sub, mul]
TERMINALS = [Th_in[0], Th_in[1], Tc_out[0], Tc_out[1], Tc_in, 0]  # "0" represents the random number generator
# [Th_in[0], Th_in[1], Tc_out[0], Tc_out[1], Tc_in, 0]

class GPTree:
    def __init__(self, data = None, left = None, right = None):
        self.data  = data
        self.left  = left
        self.right = right
        
    def node_label(self): # string label
        if (self.data in FUNCTIONS):
            return self.data.__name__
        else: 
            return str(self.data)
    
    def print_tree(self, prefix = ""): # textual printout
        print("%s%s" % (prefix, self.node_label()))        
        if self.left:  self.left.print_tree (prefix + "   ")
        if self.right: self.right.print_tree(prefix + "   ")

    def expr_tree(self): 
        if (self.data in FUNCTIONS): 
            return self.data(self.left.expr_tree(), self.right.expr_tree())
        elif self.data == 'Tc_out[0]': 
          return 'Tc_out[0]'
        elif self.data == 'Tc_out[1]': 
          return 'Tc_out[1]'
        elif self.data == 'Th_out[0]': 
          return 'Th_out[0]'
        elif self.data == 'Th_out[1]': 
          return 'Th_out[1]'
        elif self.data == 'Th_in[0]': 
          return 'Th_in[0]'
        elif self.data == 'Th_in[1]': 
          return 'Th_in[1]'
        elif self.data == 'Tc_in': 
          return 'Tc_in'
        elif self.data == '(Tc_out[0] - Tc_in)/(Th_in[0] - Tc_in)':
          return  '(Tc_out[0] - Tc_in)/(Th_in[0] - Tc_in)'
        elif self.data == '(Tc_out[1] - Tc_in)/(Th_in[1] - Tc_in)':
          return  '(Tc_out[1] - Tc_in)/(Th_in[1] - Tc_in)'
        else: return self.data
            
    def random_tree(self, grow, max_depth, depth = 0): # create random tree using either grow or full method
        if depth < MIN_DEPTH or (depth < max_depth and not grow): 
            self.data = FUNCTIONS[randint(0, len(FUNCTIONS)-1)]
        elif depth >= max_depth:
            content = TERMINALS[randint(0, len(TERMINALS)-1)]
            if isinstance(content, MX):
                self.data = content
            else:
                self.data = randint(0,100) 
        else: # intermediate depth, grow
            if random () > 0.5: 
                self.data = TERMINALS[randint(0, len(TERMINALS)-1)]
            else:
                self.data = FUNCTIONS[randint(0, len(FUNCTIONS)-1)]
        if self.data in FUNCTIONS:
            self.left = GPTree()          
            self.left.random_tree(grow, max_depth, depth = depth + 1)            
            self.right = GPTree()
            self.right.random_tree(grow, max_depth, depth = depth + 1)

    def mutation(self):
        if random() < PROB_MUTATION: # mutate at this node
            self.random_tree(grow = True, max_depth = 2)
        elif self.left: self.left.mutation()
        elif self.right: self.right.mutation() 

    def size(self): # tree size in nodes
        if self.node_label() in str(TERMINALS): return 1
        l = self.left.size()  if self.left  else 0
        r = self.right.size() if self.right else 0
        return 1 + l + r

    def build_subtree(self): # count is list in order to pass "by reference"
        t = GPTree()
        t.data = self.data
        if self.left:  t.left  = self.left.build_subtree()
        if self.right: t.right = self.right.build_subtree()
        return t
                        
    def scan_tree(self, count, second): # note: count is list, so it's passed "by reference"
        count[0] -= 1            
        if count[0] <= 1: 
            if not second: # return subtree rooted here
                return self.build_subtree()
            else: # glue subtree here
                self.data  = second.data
                self.left  = second.left
                self.right = second.right
        else:  
            ret = None              
            if self.left  and count[0] > 1: ret = self.left.scan_tree(count, second)  
            if self.right and count[0] > 1: ret = self.right.scan_tree(count, second)  
            return ret

    def crossover(self, other): # xo 2 trees at random nodes
        if random() < XO_RATE:
            second = other.scan_tree([randint(1, other.size())], None) # 2nd random subtree
            self.scan_tree([randint(1, self.size())], second) # 2nd subtree "glued" inside 1st tree
# end class GPTree
                   
def init_population(): # ramped half-and-half
    pop = []
    for md in range(3, MAX_DEPTH + 1):
        for i in range(int(POP_SIZE/6)):
            t = GPTree()
            t.random_tree(grow = True, max_depth = md) # grow
            pop.append(t) 
        for i in range(int(POP_SIZE/6)):
            t = GPTree()
            t.random_tree(grow = False, max_depth = md) # full
            pop.append(t) 
    return pop

def fitness(individual):
    try:
        expr = individual.expr_tree()
        try: 
            isinstance(float(expr),float)
            return 0
        except RuntimeError:
            f5 = expr
            f5_eval = float(evalf(substitute(f5,vertcat(Th_in,Tc_out,Tc_in),x_nom)))
            opts = {}
            opts["ipopt.max_iter"] = 200
            opts["ipopt.print_level"] = 0
            opts["show_eval_warnings"] = 0
            opts["print_time"] = 0
            temp = 0
            for i in range(0, par.shape[0]):
                lim0 = par[i,0]
                lim1 = par[i,1]
                lim2 = par[i,2]
                lim3 = par[i,3]
                lim4 = par[i,4]
                lim5 = par[i,5]
                lim6 = par[i,6]
                lim7 = par[i,7]
                limtemp = max(lim2,lim3)
                
                system = vertcat(f1,f2,f3,f4,f5)
                system = substitute(system,vertcat(Tc_in,wc,Th_in,wh,UA),vertcat(lim0,lim1,lim2,lim3,lim4,lim5,lim6,lim7))
                solver = casadi.nlpsol('solver','ipopt',dict(x = vertcat(Tc_out,T,Th_out,u,ulast), f = 0, g = system),opts)
                res = solver(x0 = [110,200,100,100,124,0.8,0.2], lbx = [lim0,lim0,lim0,lim0,lim0,0,0], ubx = [lim2,lim3,limtemp,lim2,lim3,1,1], lbg = [0,0,0,0,0,0,f5_eval], ubg = [0,0,0,0,0,0,f5_eval])
                if solver.stats()['return_status'] != 'Solve_Succeeded':
                    break
                else:
                    temp += float(res['x'][2])
            if solver.stats()['return_status'] == 'Solve_Succeeded':
                return temp
            else:
                return 0
    except ZeroDivisionError:
        return 0

def selection(population, fitnesses): # select one individual using tournament selection
    tournament = [randint(0, len(population)-1) for i in range(TOURNAMENT_SIZE)] # select tournament contenders
    tournament_fitnesses = [fitnesses[tournament[i]] for i in range(TOURNAMENT_SIZE)]
    return deepcopy(population[tournament[tournament_fitnesses.index(max(tournament_fitnesses))]]) 
            
def main():      
    # init stuff
    population= init_population() 
    best_of_run = None
    best_of_run_f = 0
    best_of_run_gen = 0
    fitnesses = [fitness(population[i]) for i in range(POP_SIZE)]
   

    # go evolution!
    for gen in range(GENERATIONS):
        nextgen_population=[]
        for i in range(POP_SIZE):
            parent1 = selection(population, fitnesses)
            parent2 = selection(population, fitnesses)
            backup1 = deepcopy(parent1)
            parent1.crossover(parent2)
            if parent1.size() <= MAX_NODE:
                parent1.mutation()
                while parent1.size() > MAX_NODE:
                    parent1.mutation()
                nextgen_population.append(parent1)
            else:
                backup1.mutation()
                while backup1.size() > MAX_NODE:
                    backup1.mutation()
                nextgen_population.append(backup1)
        population=nextgen_population
        fitnesses = [fitness(population[i]) for i in range(POP_SIZE)]
        if max(fitnesses) > best_of_run_f:
            best_of_run_f = max(fitnesses)
            best_of_run_gen = gen
            best_of_run = deepcopy(population[fitnesses.index(max(fitnesses))])
            print("________________________")
            print("gen:", gen, ", best_of_run_f:", round(max(fitnesses),3), ", best_of_run:") 
            #best_of_run.print_tree()
            print(best_of_run.expr_tree())
        if best_of_run_f == T_opt: break   
    
    print("\n\n_________________________________________________\nEND OF RUN\nbest_of_run attained at gen " + str(best_of_run_gen) +\
          " and has f=" + str(round(best_of_run_f,3)))
    #best_of_run.print_tree()
    print(best_of_run.expr_tree())
    
if __name__== "__main__":
  main()


******************************************************************************
This program contains Ipopt, a library for large-scale nonlinear optimization.
 Ipopt is released as open source code under the Eclipse Public License (EPL).
         For more information visit http://projects.coin-or.org/Ipopt
******************************************************************************

4413.529403041951
4413.453461564757
________________________
gen: 0 , best_of_run_f: 4412.506 , best_of_run:
@1=Tc_out[1], @2=Tc_out[0], @3=Th_in[0], ((((@1-98)*(2.*@2))-((Tc_in-@3)-(@1+@3)))-(((@2*@1)+(@1+@2))-((@3-Tc_in)-(@1-Tc_in))))
________________________
gen: 1 , best_of_run_f: 4412.71 , best_of_run:
((Tc_out[0]-Tc_out[1])*(2.*Th_in[0]))
________________________
gen: 2 , best_of_run_f: 4412.71 , best_of_run:
@1=Tc_out[0], @2=Tc_out[1], @3=Th_in[0], (((@1-@2)*@3)+(((@1-@2)*(2.*@3))-(@3+Tc_in)))
________________________
gen: 4 , best_of_run_f: 4412.916 , best_of_run:
@1=Th_in[1], @2=Tc_out[0], @3=Th_

SystemError: <built-in function nlpsol> returned a result with an error set

mul
   mul
      div
         (Tc_out[1]-Tc_in)
         0
      (Th_in[0]-Tc_in)
   sub
      sub
         (Tc_out[1]-Tc_in)
         (Tc_out[0]-Tc_in)
      (Tc_out[1]-Tc_in)
